## #Tag Matters
#### To understand how tags play the role by using it on NYTimes daily and how people really react about the topic by looking at other media platforms through NYTimes tags.

In the last twelve months, 563 of tags has been appeared every single months. Espetially, the specific terms included tags are shown that there were always happened 

- General tags: 'Global Warming', 'Prices (Fares, Fees and Rates)', 'Computer Security', 'Depression (Mental)'
- Countries' name: 'China', 'Iran', 'North Korea', 'Russia'
- Specific terms included: 'Hong Kong Protests (2019)', 'Civil Rights Movement (1954-68)', 'Tax Cuts and Jobs Act (2017)', '#MeToo Movement'

In [1]:
import sys
sys.executable

'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\python.exe'

In [2]:
sys.path

['C:\\Users\\Songyup\\Hwang\\Pratt\\4th Semester\\Adv.ProjectsinVis\\Monthly-Frequency-of-NYTimes-Tag',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\python38.zip',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\DLLs',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32',
 '',
 'C:\\Users\\Songyup\\AppData\\Roaming\\Python\\Python38\\site-packages',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib\\site-packages',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib\\site-packages\\win32',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib\\site-packages\\win32\\lib',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib\\site-packages\\Pythonwin',
 'c:\\users\\songyup\\appdata\\local\\programs\\python\\python38-32\\lib\\site-packages\\IPython\\extensions',
 'C:\\Users

In [3]:
import json
import requests
import pandas as pd
import numpy as np
import operator
import time
import praw
import configparser
import re

from apiclient import discovery
from datetime import datetime, date, timedelta
from dateutil.relativedelta import relativedelta

from pytrends.request import TrendReq
from praw.models import MoreComments
from googleapiclient import discovery
from pandas.io.json import json_normalize

import pprint

In [4]:
from sqlalchemy import create_engine
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import Table, Column, Integer, String, MetaData, ForeignKey

from sqlalchemy.orm import sessionmaker

In [5]:
from sqlalchemy import *
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy.sql import *
from sqlalchemy.orm import relationship

In [6]:
# Use CofigParser to safely store the password or key
config = configparser.ConfigParser()
config.read('key_pair.ini')

Times_key = config['Times']['key']

Reddit_client_id = config['Reddit']['client_id']
Reddit_client_secret = config['Reddit']['client_secret']
Reddit_username = config['Reddit']['username']
Reddit_password = config['Reddit']['password']
Reddit_user_agent = config['Reddit']['user_agent']

Youtube_service_name = config['Youtube']['YOUTUBE_API_SERVICE_NAME']
Youtube_API_version = config['Youtube']['YOUTUBE_API_VERSION']
Youtube_developer_key = config['Youtube']['DEVELOPER_KEY']

### Storing Data using SQLalchemy

In [7]:
engine = create_engine('sqlite:///monthly_times_tags.db', echo=True)
Base = declarative_base()

In [8]:
class TimesTable(Base): 
    __tablename__ = 'times'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    periodeM = Column(String(25))
    frequency = Column(Integer)
    title = Column(String(255))
    date = Column(String(25))
    url = Column(String(255))
    img_URL = Column(String(255))

class GoogleTable(Base): 
    __tablename__ = 'google'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    trendDate = Column(PickleType)
    busiest = Column(String(25))
    trendIndex = Column(PickleType)
    fk_times = Column(Integer, ForeignKey("times.id", ondelete='CASCADE'), nullable=False)
    googleNTag = relationship('TimesTable')


class RedditTable(Base): 
    __tablename__ = 'reddit'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    commentCount = Column(Integer)
    
class YoutubeTable(Base): 
    __tablename__ = 'youtube'
    __table_args__ = {'extend_existing': True}

    id = Column(Integer, primary_key=True)
    tag = Column(String(255))
    viewCount = Column(Integer)
    commentCount = Column(Integer)
    likeCount = Column(Integer)

# TimesTable.__table__.create(bind=engine, checkfirst=True)
# GoogleTable.__table__.create(bind=engine, checkfirst=True)
# RedditTable.__table__.create(bind=engine, checkfirst=True)
# YoutubeTable.__table__.create(bind=engine, checkfirst=True)

### New York Times API
https://developer.nytimes.com/apis

Archive API
- Finds all articles's metadata from archive APi (about 7000 every month): title, section_name, period, url, word_count, keywords

In [38]:
def cleaning_tag(tag):
    if tag in ['Coronavirus (2019-nCoV)']:
        tag = 'Coronavirus'
    if tag in ['School Shootings and Armed Attacks']:
        tag = 'School Shootings'
    if tag in ['Midland-Odessa, Tex, Shooting (2019)', 'Dayton, Ohio, Shooting (2019)', 'El Paso, Tex, Shooting (2019)', 'El Paso', 'Dayton', 'Shooting (2019)', 'Tex']:
        tag = 'Shootings'
    if tag in ['Homosexuality and Bisexuality']:
        tag = 'Homosexuality'
    if tag in ['Biden, Joseph R Jr']:
        tag = 'Joe Biden'
    if tag in ['Floyd, George (d 2020)']:
        tag = 'George Floyd Protests (2020)'
    if tag in ['Trump-Ukraine Whistle-blower Complaint and Impeachment Inquiry'] or 'Ukraine' in tag:
        tag = 'Trump Ukraine Whistle blower'
    if tag in ['Black People', 'Blacks']:
        tag = 'Blacks'
    if 'Security Act (2020)' in tag:
        tag = 'Coronavirus Aid Relief and Economic Security Act'
    if 'Suleimani' in tag:
        tag = 'Qasem Soleimani'
    if 'Homicides' in tag:
        tag ='Homicides'
    if 'Buttigieg' in tag:
        tag = 'Pete Buttigieg'
    if 'Police Brutality' in tag:
        tag = 'Police Brutality'
    if 'Shutdowns' in tag:
        tag = 'Shutdowns'
    if 'Quarantine' in tag:
        tag = 'Quarantines'
    if 'Deaths' in tag:
        tag = 'Deaths'
    if 'Russian Interference in 2016' in tag:
        tag = 'Russian interference in the 2016 United States elections'
    if 'Syria' in tag:
        tag = 'Syria'    
    if tag in ['Presidential Election of 2020', 'Elections', 'United States Politics and Government', 'New York City', 'United States', 'Politics and Government', 'Weddings and Engagements', 'Books and Literature', 'Television', 'Art', 'Deaths', 'Primaries and Caucuses', '']:
        tag = ''
    return tag

In [39]:
def get_NYTimes_metadata():

    # To get most frequently used tag in NYTimes
    today = str(datetime.today())
    monthly_archive = {}
    frequent_tags_archive = {}

    for yy in reversed(range(2019, int(today[:4]) + 1)):
        if str(yy) == today[:4]:
            ends = int(today[5:7]) + 1
            start = 1
        else:
            ends = 13
            if '0' in today[5:7]:
                start = int(today[6:7]) + 1
            else:
                start = int(today[5:7]) + 1

        for mm in reversed(range(start, ends)):
            parameters = {'api-key': Times_key}           
            archived_Url = 'https://api.nytimes.com/svc/archive/v1/'+ str(yy) +'/'+ str(mm) +'.json'
            archives = requests.get(archived_Url, params=parameters).json()

            monthly_article = []
            for a in archives['response']['docs']:
                articles = {}
                articles['title'] = a['headline']['main']
                articles['pub_date'] = a['pub_date'][:10]
                articles['url'] = a['web_url']
                
                if len(a['multimedia']) !=0 and a['multimedia'][0]['url']:
                    articles['thm_img'] = 'https://static01.nyt.com/' + a['multimedia'][0]['url']
                else:
                    articles['thm_img'] = 'no_image_found'
                
                cleaning_article = map(cleaning_tag,  [''.join(tag['value']) for tag in a['keywords']])
                articles['tags'] = [changed_tag if ', ' not in changed_tag else changed_tag.replace(", ", " ") for changed_tag in cleaning_article]
                
                monthly_article.append(articles)
                
            if len(str(mm)) == 1:
                mm = '0' + str(mm)
            monthly_archive[str(yy)+'-'+str(mm)] = monthly_article
            
            count_tag = {}
            for m in monthly_article:
                for tag in m['tags']:
                    if tag != '':
                        if tag in count_tag:
                            count_tag[tag] += 1
                        else:
                            count_tag[tag] = 1   

            # This variable is what we want to get in NYTimes
            tags_with_frequency = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)[:10]
            frequent_tags_archive[str(yy)+'-'+str(mm)] = tags_with_frequency

    return monthly_archive, frequent_tags_archive

In [40]:
monthly_archive = get_NYTimes_metadata()[0]
frequent_tags_archive = get_NYTimes_metadata()[1]

In [41]:
frequent_tags_archive

{'2020-08': [('Coronavirus', 1202),
  ('Trump Donald J', 722),
  ('Blacks', 494),
  ('Joe Biden', 403),
  ('Quarantines', 394),
  ('Democratic Party', 349),
  ('Democratic National Convention', 245),
  ('Coronavirus Reopenings', 221),
  ('Republican Party', 205),
  ('Race and Ethnicity', 169)],
 '2020-07': [('Coronavirus', 1812),
  ('Trump Donald J', 853),
  ('Blacks', 680),
  ('Coronavirus Reopenings', 593),
  ('Quarantines', 537),
  ('George Floyd Protests (2020)', 289),
  ('Black Lives Matter Movement', 250),
  ('Race and Ethnicity', 245),
  ('Discrimination', 244),
  ('Movies', 244)],
 '2020-06': [('Coronavirus', 1735),
  ('George Floyd Protests (2020)', 1342),
  ('Blacks', 777),
  ('Trump Donald J', 760),
  ('Black Lives Matter Movement', 639),
  ('Coronavirus Reopenings', 633),
  ('Quarantines', 589),
  ('Police Brutality', 550),
  ('Discrimination', 429),
  ('Race and Ethnicity', 379)],
 '2020-05': [('Coronavirus', 2872),
  ('Quarantines', 1247),
  ('Trump Donald J', 648),
  ('S

In [12]:
monthly_archive

{'2020-08': [{'title': 'Talking to the Dead in the Sunshine State',
   'pub_date': '2020-08-01',
   'url': 'https://www.nytimes.com/2020/08/01/opinion/spiritualism-cassadaga-florida.html',
   'thm_img': 'https://static01.nyt.com/images/2020/08/01/opinion/sunday/01gerard-top/01gerard-03-articleLarge.jpg',
   'tags': ['Psychics and Fortune Tellers',
    'Grief (Emotion)',
    'Florida',
    'Religion and Belief',
    'Cassadaga Spiritualist Camp']},
  {'title': 'Ethiopian Workers Are Forced to Return Home, Some With Coronavirus',
   'pub_date': '2020-08-01',
   'url': 'https://www.nytimes.com/2020/08/01/world/africa/ethiopian-migrant-workers-coronavirus.html',
   'thm_img': 'https://static01.nyt.com/images/2020/08/02/world/02ethiopia-migrants/merlin_173729919_f42842bb-de6f-4b2d-a84e-7034e168495a-articleLarge.jpg',
   'tags': ['Coronavirus (2019-nCoV)',
    'Foreign Workers',
    'Migrant Labor (Non-Agriculture)',
    'Immigration and Emigration',
    'Quarantines',
    'Ethiopia',
    'D

In [30]:
def call_monthly_top_tags(frequent_tags_archive, number):
    monthly_top_tags = {}
    for time_period in frequent_tags_archive.keys():
        tag_only = []
        for each in frequent_tags_archive[time_period][:number]: 
            tag_only.append(each[0])
            monthly_top_tags[time_period] = tag_only
    return monthly_top_tags

In [32]:
monthly_top_tags = call_monthly_top_tags(frequent_tags_archive, 10)
monthly_top_tags

{'2020-08': ['Coronavirus (2019-nCoV)',
  'Trump Donald J',
  'Blacks',
  'Joe Biden',
  'Quarantines',
  'Democratic Party',
  'Democratic National Convention',
  'Coronavirus Reopenings',
  'Republican Party',
  'Race and Ethnicity'],
 '2020-07': ['Coronavirus (2019-nCoV)',
  'Trump Donald J',
  'Blacks',
  'Coronavirus Reopenings',
  'Quarantines',
  'George Floyd Protests (2020)',
  'Black Lives Matter Movement',
  'Race and Ethnicity',
  'Discrimination',
  'Movies']}

In [33]:
def call_unique_whole_tag_list(monthly_top_tags):
    count_tag = {}
    for periode in monthly_top_tags:
        for tag in monthly_top_tags[periode]:
            if tag != '' and tag in count_tag:
                count_tag[tag] += 1
            else:
                count_tag[tag] = 1  
    unique_whole_tag_list = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)
    unique_whole_tag_list = [tags_f for tags_f in unique_whole_tag_list]
    return unique_whole_tag_list 

In [34]:
unique_whole_tag_list = call_unique_whole_tag_list(monthly_top_tags)
unique_whole_tag_list

[('Coronavirus (2019-nCoV)', 2),
 ('Trump Donald J', 2),
 ('Blacks', 2),
 ('Quarantines', 2),
 ('Coronavirus Reopenings', 2),
 ('Race and Ethnicity', 2),
 ('Joe Biden', 1),
 ('Democratic Party', 1),
 ('Democratic National Convention', 1),
 ('Republican Party', 1),
 ('George Floyd Protests (2020)', 1),
 ('Black Lives Matter Movement', 1),
 ('Discrimination', 1),
 ('Movies', 1)]

In [15]:
def store_times(monthly_archive, frequent_tags_archive):
    multi_articles = {}
    been_used = []
    for periode in frequent_tags_archive:
        print('='*20)
        print('periode : ', periode)     
        print('='*20)
        for top_tag in frequent_tags_archive[periode]:
            for i, each in enumerate(reversed(monthly_archive[periode])):
                if top_tag[0] in multi_articles and periode in multi_articles[top_tag[0]]:
                    pass                             
                else:
                    if len(each['tags']) != 0 and top_tag[0] in each['tags'] and each['title'] not in been_used:
                        try:
                            multi_articles[top_tag[0]] = periode
                            been_used.append(each['title'])
                            
                        except Exception as e:
                            print(" = Unable insert_TimesTag: ", top_tag[0], periode, " =", e)
                            pass   
    return #multi_articles

In [16]:
store_times(monthly_archive, frequent_tags_archive)

periode :  2020-08
periode :  2020-07
periode :  2020-06
periode :  2020-05
periode :  2020-04
periode :  2020-03
periode :  2020-02
periode :  2020-01
periode :  2019-12
periode :  2019-11
periode :  2019-10
periode :  2019-09


In [17]:
dayDates = []
today = datetime.now()
dayDates.append(today.strftime("%m%d%Y"))
for i in range(0,14):
    day = today + timedelta(days=i)
    print(day)

2020-08-26 16:23:39.654123
2020-08-27 16:23:39.654123
2020-08-28 16:23:39.654123
2020-08-29 16:23:39.654123
2020-08-30 16:23:39.654123
2020-08-31 16:23:39.654123
2020-09-01 16:23:39.654123
2020-09-02 16:23:39.654123
2020-09-03 16:23:39.654123
2020-09-04 16:23:39.654123
2020-09-05 16:23:39.654123
2020-09-06 16:23:39.654123
2020-09-07 16:23:39.654123
2020-09-08 16:23:39.654123


In [18]:
datetime.today()

datetime.datetime(2020, 8, 26, 16, 23, 39, 759129)

In [19]:
today = datetime.today()
pre_month = str(today.replace(day=1) - timedelta(days=22))
pre_month

'2020-07-10 16:23:39.837134'

### Top Tags with Frequency per each Month

In [20]:
def call_monthly_top_tags(frequent_tags_archive, number):
    monthly_top_tags_with_frequency = {}
    for time_period in frequent_tags_archive.keys():
        tag_only = []
        for each in frequent_tags_archive[time_period][:number]: 
            tag_only.append(each[0])
            monthly_top_tags_with_frequency[time_period] = tag_only
    return monthly_top_tags_with_frequency

In [21]:
monthly_top10_tags = call_monthly_top_tags(frequent_tags_archive, 5)
monthly_top10_tags

{'2020-08': ['Coronavirus (2019-nCoV)',
  'Trump Donald J',
  'Blacks',
  'Joe Biden',
  'Quarantines'],
 '2020-07': ['Coronavirus (2019-nCoV)',
  'Trump Donald J',
  'Blacks',
  'Coronavirus Reopenings',
  'Quarantines'],
 '2020-06': ['Coronavirus (2019-nCoV)',
  'George Floyd Protests (2020)',
  'Blacks',
  'Trump Donald J',
  'Black Lives Matter Movement'],
 '2020-05': ['Coronavirus (2019-nCoV)',
  'Quarantines',
  'Trump Donald J',
  'Shutdowns',
  'Coronavirus Reopenings'],
 '2020-04': ['Coronavirus (2019-nCoV)',
  'Quarantines',
  'Trump Donald J',
  'Parenting',
  'Epidemics'],
 '2020-03': ['Coronavirus (2019-nCoV)',
  'Quarantines',
  'Trump Donald J',
  'Epidemics',
  'Democratic Party'],
 '2020-02': ['Trump Donald J',
  'Coronavirus (2019-nCoV)',
  'Democratic Party',
  'Sanders Bernard',
  'China'],
 '2020-01': ['Trump Donald J',
  'Trump Ukraine Whistle blower',
  'Democratic Party',
  'United States International Relations',
  'Impeachment'],
 '2019-12': ['Trump Donald J',

### Unique Tags list 

In [22]:
def call_unique_tag_list(monthly_top10_tags):
    count_tag = {}
    for periode in monthly_top10_tags:
        for tag in monthly_top10_tags[periode]:
            if tag != '' and tag in count_tag:
                count_tag[tag] += 1
            else:
                count_tag[tag] = 1  
    unique_tag_list = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)
    unique_tag_list = [tags_f for tags_f in unique_tag_list] #if tags_f[1] > 9]
    return unique_tag_list

In [23]:
unique_tag_list = call_unique_tag_list(monthly_top10_tags)
unique_tag_list

[('Trump Donald J', 12),
 ('Coronavirus (2019-nCoV)', 7),
 ('Democratic Party', 7),
 ('Quarantines', 5),
 ('Trump Ukraine Whistle blower', 5),
 ('Blacks', 4),
 ('United States International Relations', 3),
 ('Impeachment', 3),
 ('Coronavirus Reopenings', 2),
 ('Epidemics', 2),
 ('Movies', 2),
 ('Joe Biden', 1),
 ('George Floyd Protests (2020)', 1),
 ('Black Lives Matter Movement', 1),
 ('Shutdowns', 1),
 ('Parenting', 1),
 ('Sanders Bernard', 1),
 ('China', 1),
 ('Syria', 1)]

### Popular Tags that appear on every single month

In [24]:
def call_tags_appeared_every_month(monthly_archive):
    dicts = {}
    for periode in monthly_archive:
        tag_arr = []
        dicts[periode] = tag_arr
        for each in reversed(monthly_archive[periode]):
            for t in each['tags']:
                for string in re.split(r',(?=")', t):
                    if string != '' and string not in tag_arr:
                        tag_arr.append(', '.join(string.split(', ')))   
    count_tag = {}
    for tag_arr in dicts.values():
        for tag in tag_arr:
            if tag != '':
                if tag in count_tag:
                    count_tag[tag] += 1
                else:
                    count_tag[tag] = 1   
    monthly_unique_tags = sorted(count_tag.items(),key=operator.itemgetter(1),reverse=True)  
    monthly_unique_tags = [tags_f for tags_f in monthly_unique_tags if tags_f[1] > 11]
    return monthly_unique_tags  

In [25]:
tags_appeared_every_month = call_tags_appeared_every_month(monthly_archive)
tags_appeared_every_month

KeyboardInterrupt: 

### Pytrends API
https://pypi.org/project/pytrends/

Sample codes to see Google doesn't block my IP

In [ ]:
pytrends = TrendReq(hl='en-US', tz=360, timeout=(10,25))
tag_arr = ['Coronavirus (2019-nCoV)']
pytrends.build_payload(tag_arr, cat=0, timeframe='2020-04-01 ' + str(datetime.now())[:10], geo='', gprop='')
time.sleep(2)
df = pytrends.interest_over_time().reset_index()
df.head()

In [ ]:
# Get a unique tag collection for the search query
def get_trends_Tags(monthly_top10_tags): 
    today = str(datetime.today())
    pytrends = TrendReq(hl='en-US', tz=360)
    monthly_interests = {}
    
    for period in monthly_top10_tags:
        data = []
        for tag in monthly_top10_tags[period]:
            tag_arr = []
            tag_arr.append(tag)
            
            interest_over_time = {}
            try:
                pytrends.build_payload(tag_arr, cat=0, timeframe = '2019-05-01 '+ today[:10], geo='', gprop='')
                df = pytrends.interest_over_time().reset_index()
            except Exception as e:
                print(tag_arr, ', and which reason? ', e)
                pass
            
            interest_over_time['Tag'] = tag
            try:
                interest_over_time['StartDate'] = one_month_ago
                interest_over_time['EndDate'] = one_month_later
                interest_over_time['Rate'] = [rate for rate in df[tag]]
            except Exception as e:
                pass
            data.append(interest_over_time)     
        monthly_interests[period] = data
    return monthly_interests

In [ ]:
monthly_interests = get_trends_Tags(monthly_top10_tags_with_frequency)

In [ ]:
datetime.date.today()

In [ ]:
str(datetime.date.today().replace(day=1) - datetime.timedelta(days=31))

### Youtube API
https://developers.google.com/youtube/v3/docs/search/list?hl=en_US

In [ ]:
unique_tag_list = [('Joe Biden', 9),
 ('California', 6)]

In [ ]:
def call_Youtube(unique_tag_list):
    # creating Youtube Resource Object 
    youtube_object = discovery.build(Youtube_service_name, Youtube_API_version, developerKey = Youtube_developer_key)

    max_results = 2
    youtube_metadata = []
    
    for tag_frequency in unique_tag_list[:2]:
        viewCount = 0
        commentCount = 0
        likeCount = 0
        turned_off_comments = 0
        
        video = {}
        contain_stats = {}
        
        time.sleep(2)
        search_tags = youtube_object.search().list(q = tag_frequency[0], part = "id, snippet", order = 'relevance', maxResults = max_results, publishedAfter = "2020-01-01T00:00:00Z").execute() 
        time.sleep(2)
        
        for item in search_tags.get("items", []):
#             pprint.pprint(item)
            try:
                url = 'www.youtube.com/watch?v=' + item['id']['videoId']
                title = item['snippet']['title']
                img_url = item['snippet']['thumbnails']['medium']
                stats = youtube_object.videos().list(part='statistics, snippet', id=item["id"]["videoId"]).execute()
                time.sleep(2)
                viewCount = int(stats.get("items", [])[0]['statistics']['viewCount'])
#                 print('viewCount, ', viewCount)
                likeCount =  int(stats.get("items", [])[0]['statistics']['likeCount'])
#                 print('likeCount, ', likeCount) 
                commentCount = int(stats.get("items", [])[0]['statistics']['commentCount'])
#                 print('commentCount, ', commentCount)

            except Exception as e:
                print(" = Unable search Youtube : ", tag_frequency[0], " =", e)
                if e == 'commentCount':
                    new_likeCount = 0 #'Comments are turned off'
                    contain_stats['turned_off_comments'] = 0
                elif e == 'likeCount':
                    new_likeCount = 0
                elif e == 'viewCount':
                    new_viewCount = 0

            if 'viewCount' in contain_stats:
                contain_stats['viewCount'] = contain_stats['viewCount'] + viewCount
            else:
                contain_stats['viewCount'] = viewCount
            if 'commentCount' in contain_stats:
                contain_stats['commentCount'] = contain_stats['commentCount'] + commentCount
            else:
                contain_stats['commentCount'] = commentCount
            if 'likeCount' in contain_stats:
                contain_stats['likeCount'] = contain_stats['likeCount'] + likeCount
            else:
                contain_stats['likeCount'] = likeCount
            if 'turned_off_comments' in contain_stats:
                contain_stats['turned_off_comments'] = contain_stats['turned_off_comments'] + 1
            
            if tag_frequency[0] in video.keys():
                pass
            else:
                print('* ', tag_frequency[0])
                print('* ', title)
                print('* ', contain_stats['viewCount'])
                print('-'*20, )
                video['tag'] = tag_frequency[0]
                video['url'] = url
                video['title'] = title
                video['img_url'] = img_url
                video['stats'] = contain_stats
                
        youtube_metadata.append(video)
        
    return youtube_metadata

In [ ]:
youtube_metadata = call_Youtube(unique_tag_list)

In [ ]:
youtube_metadata

In [ ]:
for each_youtube in youtube_metadata:
    unique_tag = list(each_youtube.keys())[0]
    print(unique_tag)

## Not using anymore

- Top Stories API: (about 30 articles by 7 days): title, pub_date, url, section, des_facet, geo_facet
- Newswire API: Finds by Archive API's url : des_facet
- Most Popular API
- Top Stories API, Times Tags API, Community API

### Reddit API
https://praw.readthedocs.io/en/latest/

In [ ]:
nltk.download('averaged_perceptron_tagger')

In [ ]:
def get_reddit_comments(overall_Unique_tag_with_frequency):
    
    reddit = praw.Reddit(client_id = Reddit_client_id,
                         client_secret = Reddit_client_secret,
                         username = Reddit_username,
                         password = Reddit_password,
                         user_agent = Reddit_user_agent)
#     times_metadata = {'2020-04':['Coronavirus (2019-nCoV)', 'Quarantines', 'Parenting'], '2019-04': ['China', 'Epidemics', 'Deaths (Fatalities)']}

    reddit_metadata = []
    for tag_frequency in overall_Unique_tag_with_frequency:
        subreddit = reddit.subreddit('all')
        time.sleep(2)

        each_tag = {}
        for i, post in enumerate(subreddit.search(tag_frequency[0], sort='relevance', syntax='lucene', limit=3)):
            count = 0;
            if not post.stickied:
                each_tag['Tag'] = tag_frequency[0]
#                 print('* *',tag_frequency[0])
#                 each_tag['Title'] = post.title
#                 each_tag['CreatedAt'] = datetime.fromtimestamp(post.created_utc).isoformat()[:10]
#                 each_tag['DiscussionAbout'] = post.url
#                 print('* * *', post.url)
                each_tag_comments = post.comments.list()
                comments_arr = []
                for comment in each_tag_comments:
                    if isinstance(comment, MoreComments):
                        continue
                    comments_arr.append(comment.body)
                    count = count + len(comments_arr)
                each_tag['comments'] = count

        reddit_metadata.append(each_tag)
                    
    return reddit_metadata

In [ ]:
def get_reddit_Posts(times_metadata):   
#     result = {}
#     for time_period in times_metadata:
#         data = []
#         for each in times_metadata[time_period]:     
#             data.append(each['Tag'])
#             result[time_period] = data  
            
    reddit = praw.Reddit(client_id = Reddit_client_id,
                         client_secret = Reddit_client_secret,
                         username = Reddit_username,
                         password = Reddit_password,
                         user_agent = Reddit_user_agent)
    result = {'2020-04':['Coronavirus (2019-nCoV)', 'Quarantines', 'Parenting'], '2019-04': ['China', 'Epidemics', 'Deaths (Fatalities)']}
 
    reddit_metadata = []
    for period in result:
        print(period + ': ', len(result[period]))
        reddit_posts = {}
        add_post_arr = []
        for tag in result[period]:
            subreddit = reddit.subreddit('all')
            time.sleep(2)
            for i, post in enumerate(subreddit.search(tag, sort='relevance', syntax='lucene', limit=100)):
                if not post.stickied:
                    each_tag = {}
                    each_tag['Tag'] = tag
#                     print('--1--',tag)
                    each_tag['Title'] = post.title
                    each_tag['CreatedAt'] = datetime.fromtimestamp(post.created_utc).isoformat()[:10]
                    each_tag['DiscussionAbout'] = post.url
                    each_tag['Ups'] = post.ups
                    each_tag['Downs'] = post.downs
                    add_post_arr.append(each_tag)
        reddit_posts[period] = add_post_arr
        reddit_metadata.append(reddit_posts)
#         print('--2--',reddit_metadata)
    
#     add_tag = {}
#     for item in reddit_metadata:
#         for period in item: 
#             monthly_posts = []
#             byTime = {}
            
#             for each_post in item[period]:
#                 each_post['CreatedAt'] = each_post['CreatedAt'][:7]

#                 if each_post['Tag'] in add_tag:
#                     if each_post['CreatedAt'] in byTime:
#                         byTime[each_post['CreatedAt']][0] += 1
#                         byTime[each_post['CreatedAt']][1] += each_post['Ups']
#                     else:
#                         add_freq_votes = []
#                         byTime[each_post['CreatedAt']] = add_freq_votes
#                         add_freq_votes.append(1)
#                         add_freq_votes.append(each_post['Ups'])
#                 else:
#                     add_tag[each_post['Tag']] = byTime
#                     if each_post['CreatedAt'] in byTime:
#                         byTime[each_post['CreatedAt']][0] += 1
#                         byTime[each_post['CreatedAt']][1] += each_post['Ups']
#                     else:
#                         add_freq_votes = []
#                         byTime[each_post['CreatedAt']] = add_freq_votes
#                         add_freq_votes.append(1)
#                         add_freq_votes.append(each_post['Ups'])
# #                     print('--1--', add_tag)
#             monthly_posts.append(add_tag)
# #             print('--2--', monthly_posts)
    
# #     print('--3--', monthly_posts)
    return reddit_metadata

In [ ]:
frequent_tags_archive = {'2020-04': [('Coronavirus (2019-nCoV)', 3591),
  ('Quarantines', 822)]}

In [ ]:
 # reddit = praw.Reddit(client_id = Reddit_client_id,
    #                      client_secret = Reddit_client_secret,
    #                      username = Reddit_username,
    #                      password = Reddit_password,
    #                      user_agent = Reddit_user_agent)
    # reddit_metadata = []
    
    # # Store numbers of each Reddit's comments into DB
    # try:
    #     print('Check tag existing on Reddit: ', tag_frequency[0])
    #     subreddit = reddit.subreddit('all')
    #     time.sleep(2)

    #     each_tag = {}
    #     for post in subreddit.search(tag_frequency[0], sort='relevance', syntax='lucene', time_filter='month', limit=max_results):
    #         count = 0;
    #         if not post.stickied:
    #             each_tag['Tag'] = tag_frequency[0]
    #             each_tag_comments = post.comments.list()
    #             comments_arr = []
    #             for comment in each_tag_comments:
    #                 if isinstance(comment, MoreComments):
    #                     continue
    #                 comments_arr.append(comment.body)
    #                 count = count + len(comments_arr)
    #             each_tag['commentCount'] = count
    # except Exception as e:
    #     print(" = Unable search Reddit : ", tag_frequency[0], " =")
    #     pass
    
    # reddit_metadata.append(each_tag)

    # print('= reddit_metadata =', reddit_metadata)

    # for each_reddit in reddit_metadata:    
    #     try:
    #         insert_Reddit = RedditTable(
    #             tag=each_reddit['tag'],
    #             commentCount=each_reddit['commentCount']
    #         )
    #         session.add(insert_Reddit)

    #     except Exception as e:
    #         print(" = Unable insert_Reddit to DB : ", tag_frequency[0], " =")
    #         pass

In [ ]:
def get_sentimental_chart(reddit_metadata):
    tags_metadata = []
    for single_tag in reddit_metadata:
        tag_sentiment = {}
        avg_polarity = 0
        pos_count = 0
        neg_count = 0
        neutral_count = 0
        for single_comment in single_tag['Comments']: 
            
            # Get Word Sentimental analysis
            blobed_word = TextBlob(single_comment)
            if blobed_word.sentiment.polarity > 0:
                pos_count += 1
            elif blobed_word.sentiment.polarity == 0:
                neutral_count += 1
            else:
                neg_count += 1      
            avg_polarity += blobed_word.sentiment.polarity
            
            tag_sentiment['tag'] = single_tag['Tag']    
            tag_sentiment['avg_polarity'] = avg_polarity / len(single_tag['Comments'])
            tag_sentiment['pos_count'] = pos_count
            tag_sentiment['neg_count'] = neg_count
            tag_sentiment['neutral_count'] = neutral_count
            
            # Get Adjective words' frequencies
            adgs_arr = []
            for blobed_tags in blobed_word.tags:
                if blobed_tags[1] in ['JJ', 'JJR', 'JJS']:
                    adgs_arr.append(blobed_tags[0])
            adg_frequency = {}
            for adg in adgs_arr: 
                if adg in adg_frequency:
                    adg_frequency[adg] += 1
                else:
                    adg_frequency[adg] = 1 
            tag_sentiment['adg_frequency'] = sorted(adg_frequency.items(),key=operator.itemgetter(1),reverse=True)[:3]       
        tags_metadata.append(tag_sentiment)
        
    return tags_metadata